In [3]:
# -*- coding: utf-8 -*-

import re
import requests
from pandas import DataFrame

#####将网页中老师姓名与其网址对应
url1 = "http://finance.jxufe.edu.cn/news-list-jiaoshou-1.html"
url2 = "http://finance.jxufe.edu.cn/news-list-jiaoshou-2.html"


def get_teachers_href(url):  # 定义函数
    r = requests.get(url)  # 读取网页内容
    html_text = r.text  # html赋给文本
    searchObj_s = re.findall(r'<div class="textlist">.*?</div>', html_text)  # 正则表达式提取网页代码中老师的信息
    links_teacher = {}  # 字典
    for item in searchObj_s:  # 循环
        name = item[81:-10]  # 老师的名字所在字符位置，注意左闭右开
        name = name.replace(' ', '')  # 删除名字中所有空格
        href = item[32:79]  # 老师的网址所在字符位置，注意左闭右开
        links_teacher[name] = href  # 将名字与网址对应
    return (links_teacher)


def get_teachers_name(url):
    r = requests.get(url)  # 读取网页内容
    html_text = r.text  # html赋给文本
    searchObj_s = re.findall(r'<div class="textlist">.*?</div>', html_text)  # 正则表达式提取网页代码中老师的信息
    namelist = []  # 字典
    for item in searchObj_s:
        name = item[81:-10]  # 老师的名字所在字符位置，注意左闭右开
        name = name.replace(' ', '')  # 删除名字中所有空格
        namelist.append(name)
    return namelist


###对网页使用函数
links = get_teachers_href(url1)
links1 = get_teachers_href(url2)
links.update(links1)

name_list = get_teachers_name(url1)
name_list1 = get_teachers_name(url2)
name_list.extend(name_list1)

def get_value(key, html):
    pattern = '%s</strong>.*?：?:?(.*?)</p>' % key
    searchObj = re.search(pattern, html)
    if searchObj:
        value = searchObj.group(1)
    else:
        pattern = '%s：</strong>.*?(.*?)</p>' % key
        searchObj1 = re.search(pattern, html)
        value = searchObj1.group(1)
    return (value)
def get_jiang_value(key,html):
    pattern = '%s</span></strong><.*?>：(.*?)</span>' % key
    searchObj = re.search(pattern, html)
    value = searchObj.group(1)
    return value
def get_jiang(name,html):
    xb = get_jiang_value('别', html)
    zzmm = get_jiang_value('貌', html)
    byyx = get_jiang_value('校', html)
    byzy = get_jiang_value('业', html)
    pattern = '方式</strong>：</span><.*?>(.*?)</span>'
    searchObj = re.search(pattern, html)
    yx = searchObj.group(1)
    teacher_info = {'姓名': name,
                    '性别': xb,
                    '政治面貌': zzmm,
                    '毕业院校': byyx,
                    '毕业专业': byzy,
                    '联系方式': yx,
                    }
    return (teacher_info)
def parse_content(name,html):
    # xm = get_value('名', html)
    xb = get_value('别', html)
    zzmm = get_value('貌', html)
    byyx = get_value('校', html)
    byzy = get_value('业', html)
    if(xb==''):
        xb = '网页无显示'
    if(name=='彭玉镏'):
        pattern = '邮箱</span></a></span></strong></span></span></strong><strong><.*?><.*?><strong>.*?</strong>(.*?)<.*?>'
        searchObj1 = re.search(pattern, html)
        yx = searchObj1.group(1)
    else:
        yx = get_value('箱',html)

    teacher_info = {'姓名': name,
                    '性别': xb,
                    '政治面貌': zzmm,
                    '毕业院校': byyx,
                    '毕业专业': byzy,
                    '联系方式': yx,
                   }
    return (teacher_info)

jiao_shou = []
for item in name_list:
    # print(item)
    if (item != '蒋崇辉'):
        r=requests.get(links[item])
        html = r.text
        teacher_info = parse_content(item,html)
    else:
        r = requests.get(links[item])
        html = r.text
        teacher_info = get_jiang(item,html)
    jiao_shou.append(teacher_info)
df1 = DataFrame(jiao_shou)
display(df1)

姓名     性别  政治面貌             毕业专业         毕业院校                   联系方式
0    曹邓      女  中共党员              管理学       江西财经大学   laotoutou@aliyun.com
1   陈春霞      女    群众              金融学       江西财经大学        new9360@163.com
2   陈家洪      男  中共党员     经济统计（证券研究方向）       江西财经大学         jxmcjh@126.com
3   桂荷发      男  民进会员              金融学       中国人民大学        guihefa@163.com
4   黄飞鸣      男  民革党员              金融学         厦门大学       172348582@qq.com
5   胡援成      男  中共党员              金融学         厦门大学          hu-yc@163.com
6   吕江林      男  中共党员              经济学       中南财经大学        ljl5983@126.com
7   刘兴华      男  中共党员             世界经济         厦门大学        lxh7572@126.com
8   凌爱凡      男  中共党员             计算数学       西安交通大学       aiffling@163.com
9   彭玉镏      男  中共党员              金融学       上海财经大学     pengyuliu@sohu.com
10  蒋崇辉      男  中共党员  管理科学与工程（金融工程方向）       电子科技大学        jch0920@163.com
11  孙爱琳      女  中共党员            政治经济学         浙江大学        sal6660@126.com
12   王辉  网页无显示  中共党员              财政学       江西财经大学         wh6660@126.com
13   汪洋      男  中共党员              金融学       上海财经大学  wangyang@jxufe.edu.cn
14   肖峻      男    民进            管理学博士  同济大学经济与管理学院    xiao_jun913@163.com
15  杨玉凤      女  民主党派              金融学       江西财经大学      xialuoren@126.com
16   杨荣      女  中共党员              金融学       江西财经大学   yonghongyang@163.com
17   严武      男    党员              经济学       江西财经大学       923108620@qq.com